In [1]:
# -*- coding: utf-8 -*-
# !/usr/bin/env python

print("开始导入模块...")

import torch
import os
import soundfile as sf
from IPython.display import Audio, display, FileLink
import traceback
import uuid # 用于生成唯一文件名
import numpy as np # ACE-Step 内部可能会用到

# --- 检查 PyTorch (您的环境是 torch==2.7.0) ---
print(f"PyTorch 版本: {torch.__version__}")
if torch.cuda.is_available():
    print(f"CUDA 可用. GPU: {torch.cuda.get_device_name(0)}")
else:
    print("警告: CUDA 不可用。推理将使用 CPU 且非常缓慢。")

# ---------------------------------------------------------------------------
# 关键: 导入 ACE-Step 的 Pipeline 类
# ---------------------------------------------------------------------------
try:
    from acestep.pipeline_ace_step import ACEStepPipeline
    print("ACEStepPipeline 导入成功。")
except ImportError as e:
    print(f"错误: 无法导入 ACEStepPipeline: {e}")
    print("请确保您已在当前 Conda 环境中正确安装了 ACE-Step 库。")
    print("例如，通过 `pip install git+https://github.com/ace-step/ACE-Step.git`")
    raise

print("模块导入完成。")

开始导入模块...
PyTorch 版本: 2.7.0+cu126
CUDA 可用. GPU: NVIDIA A40


/home/jovyan/emoheal_conda_v2/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


ACEStepPipeline 导入成功。
模块导入完成。


In [2]:
# --- ACEStepPipeline 初始化所需参数 ---

# !!! 【模型权重 CHECKPOINT_PATH 配置 - 请仔细阅读并选择一种方式】!!!
# 根据 ACE-Step 官方描述:
# 1. 如果设置了路径且该路径下有模型，则加载模型。
# 2. 如果设置了路径但该路径下没有模型，则自动下载模型到该路径。
# 3. 如果 checkpoint_path 未设置 (或设为 None)，则自动下载模型到默认路径 `~/.cache/ace-step/checkpoints`。

# --- 方式 A (推荐首次使用或希望使用默认下载路径): ---
# 将 CHECKPOINT_PATH 设置为 None，让 ACE-Step 自动下载到默认位置。
# 第一次运行会比较慢，因为它需要下载模型。网络需要通畅。
CHECKPOINT_PATH = None

# --- 方式 B (希望将模型下载或存放到您指定的、可写的位置): ---
# 设置一个您希望 ACE-Step 下载模型到的目录。如果目录为空，ACE-Step会尝试下载到这里。
# 如果此路径下已有模型，则会加载它们。
# 请确保此路径对于运行 Notebook 的用户是可写的。
# 示例: CHECKPOINT_PATH = "/home/jovyan/my_acestep_models" # 【请取消注释并修改为您希望的路径】

# --- 方式 C (如果您已通过其他方式下载或获取了模型，并存放到特定位置): ---
# 直接指向您模型权重所在的目录。
# 示例: CHECKPOINT_PATH = "/path/to/your/ALREADY_DOWNLOADED_ace_step_checkpoint_directory" # 【请取消注释并修改】

# (请确保上面三种方式中，只有一种是被取消注释并生效的)


# --- 设备和精度配置 (与 infer.py 中的选项对应) ---
DEVICE_ID = 0  # 使用的 GPU ID
BF16 = True    # 是否使用 bfloat16 (推荐用于 A100)
TORCH_COMPILE = True # 是否使用 torch.compile (推荐用于 A100，您的环境已安装 Triton)
CPU_OFFLOAD = False  # 是否使用 CPU offloading
OVERLAPPED_DECODE = True # 是否使用重叠解码

# --- 输出目录配置 (Notebook 端) ---
NOTEBOOK_OUTPUT_DIR = "acestep_direct_outputs"
os.makedirs(NOTEBOOK_OUTPUT_DIR, exist_ok=True)

print("Pipeline 初始化参数配置完成。")
if CHECKPOINT_PATH is None:
    print("CHECKPOINT_PATH 设置为 None。ACE-Step 将尝试自动下载模型到默认缓存路径 (如 ~/.cache/ace-step/checkpoints)。")
    print("首次运行或模型未缓存时，会因下载模型而耗时较长。请确保网络通畅。")
elif not os.path.exists(CHECKPOINT_PATH):
    print(f"指定的 CHECKPOINT_PATH '{CHECKPOINT_PATH}' 当前不存在。")
    print("ACE-Step 将尝试自动下载模型到此路径。请确保此路径可写且磁盘空间充足。")
    print("首次运行或模型未在此路径时，会因下载模型而耗时较长。")
else: # CHECKPOINT_PATH 是一个存在的路径
    print(f"CHECKPOINT_PATH 设置为: {CHECKPOINT_PATH}。")
    print("ACE-Step 将尝试从此路径加载模型。如果模型不完整或版本不符，仍可能触发下载。")

Pipeline 初始化参数配置完成。
CHECKPOINT_PATH 设置为 None。ACE-Step 将尝试自动下载模型到默认缓存路径 (如 ~/.cache/ace-step/checkpoints)。
首次运行或模型未缓存时，会因下载模型而耗时较长。请确保网络通畅。


In [25]:
# 纯音乐版
# --- 自定义音乐生成参数 ---
# 这些参数将直接传递给 ACEStepPipeline 的 __call__ 方法

# 【【【 在这里修改为您想要的 PROMPT 和其他参数 】】】
AUDIO_DURATION = 30.0  # 音频时长（秒） <--- 您期望的30秒
PROMPT_STR = "A 30-second beautifully melancholic solo piano piece. Slow tempo (around 50 BPM), poignant melody in a minor key with rich harmonies. Evokes gentle sadness, nostalgia, and introspection, but with an underlying sense of peace."
LYRICS_STR = "" # 您的歌词，如果不需要则为空字符串

# --- 生成细节参数 (参考官方示例 output_20250512120348_0_input_params.json) ---
INFER_STEP = 60           # 推理步数
GUIDANCE_SCALE = 15.0     # CFG scale

SCHEDULER_TYPE = "euler"  # 调度器类型
CFG_TYPE = "apg"          # CFG 类型

OMEGA_SCALE = 10.0        # Granularity scale

# --- 种子设置 ---
# 方式A：每次生成不同的音乐 (推荐先尝试这个)
MANUAL_SEEDS_LIST = [] # 或者 None
# 方式B：指定特定种子以复现 (如果需要，取消注释下一行并使用您自己的种子)
# MANUAL_SEEDS_LIST = [226581098] # 这是示例中的种子，您可以改成任意整数

OSS_STEPS_LIST = []       # Optimal Step Sampling 列表，示例中为空

GUIDANCE_INTERVAL = 0.5   #
GUIDANCE_INTERVAL_DECAY = 0.0 # (0 表示在引导区间内引导强度不变)
MIN_GUIDANCE_SCALE = 3.0  #

USE_ERG_TAG = True        #
USE_ERG_LYRIC = False     # 示例中为 False，如果您的 LYRICS_STR 为空，设为 False 通常更好
USE_ERG_DIFFUSION = True  #

GUIDANCE_SCALE_TEXT = 0.0 #
GUIDANCE_SCALE_LYRIC = 0.0#

print("音乐生成参数已更新为基于官方示例的配置。")
print(f"Prompt: {PROMPT_STR}")
print(f"Lyrics: {LYRICS_STR[:100] if LYRICS_STR else '无'}")
print(f"Audio Duration: {AUDIO_DURATION}s")

音乐生成参数已更新为基于官方示例的配置。
Prompt: A 30-second beautifully melancholic solo piano piece. Slow tempo (around 50 BPM), poignant melody in a minor key with rich harmonies. Evokes gentle sadness, nostalgia, and introspection, but with an underlying sense of peace.
Lyrics: 无
Audio Duration: 30.0s


In [ ]:
# 带歌词版
# 单元格 3: 配置音乐生成参数 (加入歌词示例)

# --- 自定义音乐生成参数 ---
# 这些参数将直接传递给 ACEStepPipeline 的 __call__ 方法

# 【【【 在这里修改为您想要的 PROMPT 和 歌词 】】】
AUDIO_DURATION = 45.0  # 音频时长（秒）<--- 尝试稍长一点以便容纳歌词
PROMPT_STR = "emotional pop ballad, male vocal, piano, strings, heartfelt" # 您的音乐描述
LYRICS_STR = """
[verse]
Empty streets, the rain begins to fall
Echoes of your laughter, I recall
A faded photograph, a silent call
Wish I could turn back time, and give my all

[chorus]
Now the stars don't shine as bright
Since you walked out of my life
Just a shadow in the fading light
Lost in this endless, lonely night

[verse]
Tried to find a reason, a way to understand
Like building castles on a shifting sand
Every promise broken, slipped right through my hand
A story of a love that wasn't planned

[chorus]
And the stars don't shine as bright
Since you walked out of my life
Just a shadow in the fading light
Lost in this endless, lonely night

[bridge]
Maybe someday, the pain will start to fade
And these memories, a softer serenade
But until then, I'll walk this path I've made
A lonely traveler, in this love charade

[chorus]
Still the stars don't shine as bright
Since you walked out of my life
Just a shadow in the fading light
Lost in this endless, lonely night
"""

# --- 生成细节参数 (参考官方示例 output_20250426093146_0_input_params.json，这是一个带歌词的 R&B 示例) ---
# 您可以从这个示例或其他包含歌词的示例中借鉴参数
# output_20250426093146_0_input_params.json (r&b, soul, funk/soul with lyrics)
INFER_STEP = 60           #
GUIDANCE_SCALE = 15.0     #

SCHEDULER_TYPE = "euler"  #
CFG_TYPE = "apg"          #

OMEGA_SCALE = 10.0        #

# --- 种子设置 ---
# 方式A：每次生成不同的音乐
MANUAL_SEEDS_LIST = [] # 或者 None
# 方式B：指定特定种子以复现 (如果需要，取消注释下一行并使用您自己的种子)
# MANUAL_SEEDS_LIST = [2853131993] # 这是上述 R&B 示例中的种子

OSS_STEPS_LIST = []       # 示例中为空

GUIDANCE_INTERVAL = 0.5   #
GUIDANCE_INTERVAL_DECAY = 0.0 #
MIN_GUIDANCE_SCALE = 3.0  #

# --- ERG (Entropy Rectifying Guidance) 参数 ---
# 当有歌词时，`use_erg_lyric` 设为 True 可能会让模型更关注歌词内容
USE_ERG_TAG = True        #
USE_ERG_LYRIC = True      # <--- 对于有歌词的生成，可以尝试 True
USE_ERG_DIFFUSION = True  #

# --- 特定引导强度 (通常在不使用标准 guidance_scale 时调整，或者用于更细致的控制) ---
# 示例中这两个通常为0，让主 guidance_scale 控制
GUIDANCE_SCALE_TEXT = 0.0 # 通常为 0.0
GUIDANCE_SCALE_LYRIC = 0.0# 通常为 0.0
# 如果您想特别增强歌词或文本的引导，可以尝试在这里设置大于1的值，但注意官方UI提示：
# "When guidance_scale_lyric > 1 and guidance_scale_text > 1, the guidance scale will not be applied."
# 这意味着如果这两个都大于1，主 `GUIDANCE_SCALE` 可能失效，转而由这两个参数控制。
# 在 `output_20250512171227_0_input_params.json` (J-Pop Rap) 示例中，`guidance_scale_text` 为 0.7，`guidance_scale_lyric` 为 1.5。
# 您可以根据需要实验。对于初次尝试，保持为0，让主 `GUIDANCE_SCALE` 生效即可。

print("音乐生成参数配置完成（包含歌词）。")
print(f"Prompt: {PROMPT_STR}")
print(f"Lyrics: \n{LYRICS_STR}")
print(f"Audio Duration: {AUDIO_DURATION}s")

In [13]:
# 全局变量用于存储 Pipeline 实例
_acestep_pipeline_instance = None

def get_acestep_pipeline(checkpoint_dir_param, bf16_param, torch_compile_flag_param, 
                         cpu_offload_flag_param, overlapped_decode_flag_param, 
                         device_id_val_param, force_reload=False):
    """
    初始化并返回 ACEStepPipeline 实例。
    """
    global _acestep_pipeline_instance
    if _acestep_pipeline_instance is not None and not force_reload:
        print("返回已存在的 ACEStepPipeline 实例。")
        return _acestep_pipeline_instance

    print(f"正在初始化 ACEStepPipeline...")
    # checkpoint_dir_param 可以是 None (下载到默认位置)，也可以是指定路径 (下载到该路径或从中加载)
    if checkpoint_dir_param is None:
        print(f"  Checkpoint Dir: None (将使用默认下载路径)")
    else:
        print(f"  Checkpoint Dir: {checkpoint_dir_param}")
        if not os.path.exists(checkpoint_dir_param):
             print(f"    (注意: 此路径当前不存在，ACE-Step将尝试下载到这里)")


    print(f"  Device ID: {device_id_val_param}")
    print(f"  BF16: {bf16_param}, Torch Compile: {torch_compile_flag_param}")
    print(f"  CPU Offload: {cpu_offload_flag_param}, Overlapped Decode: {overlapped_decode_flag_param}")

    os.environ["CUDA_VISIBLE_DEVICES"] = str(device_id_val_param)

    try:
        _acestep_pipeline_instance = ACEStepPipeline(
            checkpoint_dir=checkpoint_dir_param, # 直接传递用户配置的路径 (可以是None)
            dtype="bfloat16" if bf16_param else "float32",
            torch_compile=torch_compile_flag_param,
            cpu_offload=cpu_offload_flag_param,
            overlapped_decode=overlapped_decode_flag_param
        )
        print("ACEStepPipeline 初始化/加载成功。")
        return _acestep_pipeline_instance
    except Exception as e:
        print(f"ACEStepPipeline 初始化失败: {e}")
        print("常见原因可能包括：")
        print("  - 网络问题导致模型下载失败。")
        print("  - 指定的 checkpoint_path 无法写入 (如果尝试下载到该路径)。")
        print("  - 磁盘空间不足。")
        print("  - ACE-Step 库内部错误或依赖问题。")
        traceback.print_exc()
        _acestep_pipeline_instance = None
        return None

def generate_music_directly(
    pipeline_instance: ACEStepPipeline,
    audio_duration_val: float, prompt_val: str, lyrics_val: str, infer_step_val: int,
    guidance_scale_val: float, scheduler_type_val: str, cfg_type_val: str,
    omega_scale_val: float, manual_seeds_list_val: list, guidance_interval_val: float,
    guidance_interval_decay_val: float, min_guidance_scale_val: float,
    use_erg_tag_val: bool, use_erg_lyric_val: bool, use_erg_diffusion_val: bool,
    oss_steps_list_val: list, guidance_scale_text_val: float,
    guidance_scale_lyric_val: float, output_dir: str,
    filename_prefix: str = "acestep_direct_gen"
):
    if pipeline_instance is None:
        print("错误: ACEStepPipeline 实例无效。无法生成音乐。")
        return None

    manual_seeds_str = ", ".join(map(str, manual_seeds_list_val))
    oss_steps_str = ", ".join(map(str, oss_steps_list_val))
    unique_suffix = uuid.uuid4().hex[:8]
    output_filename = f"{filename_prefix}_{unique_suffix}.wav"
    save_path_full = os.path.join(output_dir, output_filename)

    print(f"\n开始生成音乐...")
    print(f"  输出路径: {save_path_full}")
    # (其他打印参数的语句可以保持不变)
    try:
        pipeline_instance(
            audio_duration=audio_duration_val, prompt=prompt_val, lyrics=lyrics_val,
            infer_step=infer_step_val, guidance_scale=guidance_scale_val,
            scheduler_type=scheduler_type_val, cfg_type=cfg_type_val,
            omega_scale=omega_scale_val, manual_seeds=manual_seeds_str,
            guidance_interval=guidance_interval_val,
            guidance_interval_decay=guidance_interval_decay_val,
            min_guidance_scale=min_guidance_scale_val, use_erg_tag=use_erg_tag_val,
            use_erg_lyric=use_erg_lyric_val, use_erg_diffusion=use_erg_diffusion_val,
            oss_steps=oss_steps_str, guidance_scale_text=guidance_scale_text_val,
            guidance_scale_lyric=guidance_scale_lyric_val, save_path=save_path_full
        )
        print(f"音乐生成调用完成。文件应已保存到: {save_path_full}")
        if os.path.exists(save_path_full):
            return save_path_full
        else:
            print(f"错误: 文件在预期路径 '{save_path_full}' 未找到。生成可能失败。")
            return None
    except Exception as e:
        print(f"音乐生成过程中发生错误: {e}")
        traceback.print_exc()
        return None

print("Pipeline 初始化和音乐生成函数定义完毕。")

Pipeline 初始化和音乐生成函数定义完毕。


In [26]:
# --- 1. 初始化 (或获取已初始化的) Pipeline 实例 ---
# 使用单元格 2 中定义的参数
pipeline = get_acestep_pipeline(
    checkpoint_dir_param=CHECKPOINT_PATH, # 可以是 None 或指定路径
    bf16_param=BF16,
    torch_compile_flag_param=TORCH_COMPILE,
    cpu_offload_flag_param=CPU_OFFLOAD,
    overlapped_decode_flag_param=OVERLAPPED_DECODE,
    device_id_val_param=DEVICE_ID,
    force_reload=False # 第一次运行时，即使是False也会加载；如果想强制重新下载/加载，设为True
)

generated_audio_filepath = None
if pipeline:
    print("\n--- 2. 准备调用音乐生成函数 ---")
    prompt_prefix_for_filename = PROMPT_STR.split(',')[0].replace(' ', '_').lower()[:20]

    generated_audio_filepath = generate_music_directly(
        pipeline_instance=pipeline,
        audio_duration_val=AUDIO_DURATION, prompt_val=PROMPT_STR, lyrics_val=LYRICS_STR,
        infer_step_val=INFER_STEP, guidance_scale_val=GUIDANCE_SCALE,
        scheduler_type_val=SCHEDULER_TYPE, cfg_type_val=CFG_TYPE,
        omega_scale_val=OMEGA_SCALE, manual_seeds_list_val=MANUAL_SEEDS_LIST,
        guidance_interval_val=GUIDANCE_INTERVAL,
        guidance_interval_decay_val=GUIDANCE_INTERVAL_DECAY,
        min_guidance_scale_val=MIN_GUIDANCE_SCALE, use_erg_tag_val=USE_ERG_TAG,
        use_erg_lyric_val=USE_ERG_LYRIC, use_erg_diffusion_val=USE_ERG_DIFFUSION,
        oss_steps_list_val=OSS_STEPS_LIST,
        guidance_scale_text_val=GUIDANCE_SCALE_TEXT,
        guidance_scale_lyric_val=GUIDANCE_SCALE_LYRIC,
        output_dir=NOTEBOOK_OUTPUT_DIR,
        filename_prefix=prompt_prefix_for_filename
    )
else:
    print("Pipeline 初始化失败，无法进行音乐生成。请检查之前的错误信息。")
    print("如果是因为模型下载问题，请检查网络连接和目标路径的写入权限。")


# --- 3. 展示结果 ---
if generated_audio_filepath and os.path.exists(generated_audio_filepath):
    print(f"\n--- 音乐已生成并保存于: {generated_audio_filepath} ---")
    print(f"\n在线播放 (可能需要几秒钟加载): {os.path.basename(generated_audio_filepath)}")
    display(Audio(generated_audio_filepath))
    print(f"\n下载链接 (右键点击 -> '另存为...' 或直接点击):")
    display(FileLink(generated_audio_filepath))
else:
    print("\n音乐生成失败或未找到输出文件。请检查上面的错误信息。")
    if not pipeline:
         print("主要原因可能是 Pipeline 未能成功初始化。")
         print("请检查【单元格 2】中的 CHECKPOINT_PATH 设置以及【单元格 4】的初始化日志。")
    print("同时，请确认【单元格 3】中的 SCHEDULER_TYPE 和 CFG_TYPE 是 ACE-Step 支持的有效值。")

2025-06-03 17:59:44.281 | INFO     | acestep.pipeline_ace_step:__call__:1485 - Model loaded in 0.00 seconds.
2025-06-03 17:59:44.300 | INFO     | acestep.pipeline_ace_step:text2music_diffusion_process:847 - cfg_type: apg, guidance_scale: 15.0, omega_scale: 10.0
2025-06-03 17:59:44.304 | INFO     | acestep.pipeline_ace_step:text2music_diffusion_process:1072 - start_idx: 15, end_idx: 45, num_inference_steps: 60


返回已存在的 ACEStepPipeline 实例。

--- 2. 准备调用音乐生成函数 ---

开始生成音乐...
  输出路径: acestep_direct_outputs/a_30-second_beautifu_0911c245.wav


100%|██████████| 1/1 [00:00<00:00,  7.39it/s]
2025-06-03 17:59:51.666 | INFO     | acestep.pipeline_ace_step:cleanup_memory:151 - GPU Memory: 7.43GB allocated, 7.85GB reserved


音乐生成调用完成。文件应已保存到: acestep_direct_outputs/a_30-second_beautifu_0911c245.wav

--- 音乐已生成并保存于: acestep_direct_outputs/a_30-second_beautifu_0911c245.wav ---

在线播放 (可能需要几秒钟加载): a_30-second_beautifu_0911c245.wav



下载链接 (右键点击 -> '另存为...' 或直接点击):


/home/jovyan/teaching_material/Project/Final Project/TTM/acestep_direct_outputs/a_30-second_beautifu_0911c245.wav